In [3]:
from shiny import App, render, ui
from shinywidgets import output_widget, render_widget
import pandas as pd
import geopandas as gpd
import plotly.graph_objects as go
import os
import json
import shapely
from myUtils import prepData, createMap

prev things

In [4]:
current_directory = os.getcwd()
data_directory = os.path.join(current_directory, '../../data') #
file_path1 = os.path.join(data_directory, 'subZoneScore.csv')
subZoneScore = pd.read_csv(file_path1)

In [5]:
subZoneScore['geometry'] = subZoneScore['geometry'].apply(shapely.from_wkt)

In [6]:
type(subZoneScore['geometry'][0])

shapely.geometry.polygon.Polygon

In [7]:
def city_centers(subZoneScore):
    result = {}
    for index, row in subZoneScore.iterrows():
        name = row['SUBZONE_N']
        center = row['geometry'].centroid
        lat,lon = center.xy
        result[name] = {'lon':lon[0], 'lat':lat[0]}
    return result

In [36]:
area = subZoneScore[['SUBZONE_N','SHAPE_Area']]
area = pd.concat([area, pd.DataFrame({'SUBZONE_N': 'Singapore', 'SHAPE_Area': 19000})], ignore_index = True)
area

ValueError: If using all scalar values, you must pass an index

In [29]:
area.loc[area['SUBZONE_N']=='PHILLIP', 'SHAPE_Area'].values[0]

39437.9352703

In [17]:
area['SHAPE_Area'].sum()

993043846.9473157

In [8]:

city_centers(subZoneScore)

{"PEOPLE'S PARK": {'lon': 1.2823353217602231, 'lat': 103.84079245288841},
 'BUKIT MERAH': {'lon': 1.28201421407164, 'lat': 103.81858972315474},
 'CHINATOWN': {'lon': 1.2799694820446628, 'lat': 103.84368741875113},
 'PHILLIP': {'lon': 1.2852768433137967, 'lat': 103.84865417632443},
 'RAFFLES PLACE': {'lon': 1.2837200002431797, 'lat': 103.85100738198886},
 'CHINA SQUARE': {'lon': 1.2843864299613021, 'lat': 103.84688332410562},
 'TIONG BAHRU': {'lon': 1.2838795305485389, 'lat': 103.83139275944372},
 'BAYFRONT SUBZONE': {'lon': 1.2833347252458214, 'lat': 103.85853376179658},
 'TIONG BAHRU STATION': {'lon': 1.2840299054555744, 'lat': 103.82682636121685},
 'CLIFFORD PIER': {'lon': 1.28556190580745, 'lat': 103.85469937473877},
 'MARINA SOUTH': {'lon': 1.2805312989831166, 'lat': 103.8656285332346},
 "PEARL'S HILL": {'lon': 1.2856127997411004, 'lat': 103.8394202366354},
 'BOAT QUAY': {'lon': 1.2873546011306893, 'lat': 103.84818906113482},
 'HENDERSON HILL': {'lon': 1.2869848253405956, 'lat': 10

In [9]:
subZoneScore.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 336 entries, 0 to 335
Data columns (total 26 columns):
 #   Column                                 Non-Null Count  Dtype  
---  ------                                 --------------  -----  
 0   Unnamed: 0                             336 non-null    int64  
 1   SUBZONE_N                              336 non-null    object 
 2   CA_IND                                 336 non-null    object 
 3   PLN_AREA_N                             336 non-null    object 
 4   PLN_AREA_C                             336 non-null    object 
 5   REGION_N                               336 non-null    object 
 6   SHAPE_Area                             336 non-null    float64
 7   geometry                               336 non-null    object 
 8   cyclingPathDist                        336 non-null    float64
 9   RackCount                              336 non-null    float64
 10  parkConnectorDist                      336 non-null    float64
 11  noHaza

In [10]:
subZoneScore = gpd.GeoDataFrame(subZoneScore)

In [11]:
counter = 0
ls = []
for geom in subZoneScore['geometry']:
    if type(geom) != type(subZoneScore['geometry'][0]):
        counter += 1
        ls.append(type(geom))


In [22]:
fig = go.Figure(go.Choroplethmapbox(
                   geojson=json.loads(subZoneScore.geometry.to_json()),
                   locations=subZoneScore.index,
                   colorscale="mint",
                   z=subZoneScore['score'],
                   text = subZoneScore['DESCRIPTION'],
                   hovertemplate="%{text}<br><br><span style = \"font-size: 1.2em;\"><b>Overall Score: </b>: %{z}</span>"
                   ))

fig.update_layout(
    margin ={'l':0,'t':0,'b':0,'r':0},
    mapbox = {
        'center': {'lon': 103.9, 'lat': 1.38},
        'style': "open-street-map",
        'center': {'lon': 103.9, 'lat': 1.38},
        'zoom': 15})

fig.show()